# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [ ]:
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-jamo.txt

In [5]:
!python OpenNMT-py/tools/apply_morph_en.py -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt-train-morph.txt
!python OpenNMT-py/tools/apply_morph_en.py -i OpenNMT-py/Data/tgt-valid.txt -o OpenNMT-py/Data/tgt-val-morph.txt
!python OpenNMT-py/tools/apply_morph_en.py -i OpenNMT-py/Data/tgt-test.txt -o OpenNMT-py/Data/tgt-test-morph.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [6]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-jamo.txt -train_tgt OpenNMT-py/Data/tgt-train-morph.txt -valid_src OpenNMT-py/Data/src-val-jamo.txt -valid_tgt OpenNMT-py/Data/tgt-val-morph.txt -save_data OpenNMT-py/Data/jamo2morph/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-07 08:10:26,130 INFO] Extracting features...
[2020-12-07 08:10:26,131 INFO]  * number of source features: 0.
[2020-12-07 08:10:26,131 INFO]  * number of target features: 0.
[2020-12-07 08:10:26,131 INFO] Building `Fields` object...
[2020-12-07 08:10:26,131 INFO] Building & saving training data...
[2020-12-07 08:10:39,973 INFO] Building shard 0.
[2020-12-07 08:11:56,730 INFO]  * saving 0th train data shard to OpenNMT-py/Data/jamo2morph/demo.train.0.pt.
[2020-12-07 08:11:57,863 INFO]  * tgt vocab size: 6548.
[2020-12-07 08:11:57,864 INFO]  * src vocab size: 91.
[2020-12-07 08:11:57,881 INFO] Building & saving validation data...
[2020-12-07 08:11:57,977 INFO] Building shard 0.
[2020-12-07 08:11:58,377 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/jamo2morph/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [7]:
!nvidia-smi

Mon Dec  7 08:12:28 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   26C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [8]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/jamo2morph/demo -save_model OpenNMT-py/Data/jamo2morph/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 100 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/jamo2morph'

[2020-12-07 08:12:48,423 INFO]  * src vocab size = 91
[2020-12-07 08:12:48,423 INFO]  * tgt vocab size = 6548
[2020-12-07 08:12:48,423 INFO] Building model...
[2020-12-07 08:12:54,470 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(91, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_features=51

[2020-12-07 08:12:54,638 INFO] Starting training on GPU: [0]
[2020-12-07 08:12:54,638 INFO] Start training loop and validate every 1000 steps...
[2020-12-07 08:12:54,639 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:12:54,867 INFO] number of examples: 4835
[2020-12-07 08:13:02,120 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:13:02,297 INFO] number of examples: 4835
[2020-12-07 08:13:07,544 INFO] Step 50/50000; acc:   4.08; ppl: 1529.28; xent: 7.33; lr: 0.00001; 30053/8513 tok/s;     13 sec
[2020-12-07 08:13:09,803 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:13:09,976 INFO] number of examples: 4835
[2020-12-07 08:13:17,189 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:13:17,415 INFO] number of examples: 4835
[2020-12-07 08:13:20,465 INFO] Step 100/50000; acc:   8.32; ppl: 750.08; xent: 6.62; lr: 0.00001; 30092/8404 tok/s;     26 s

[2020-12-07 08:17:12,184 INFO] number of examples: 4835
[2020-12-07 08:17:13,759 INFO] Step 950/50000; acc:  41.19; ppl: 20.10; xent: 3.00; lr: 0.00012; 26363/7436 tok/s;    259 sec
[2020-12-07 08:17:19,576 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:17:19,747 INFO] number of examples: 4835
[2020-12-07 08:17:26,602 INFO] Step 1000/50000; acc:  42.73; ppl: 17.80; xent: 2.88; lr: 0.00012; 30214/8517 tok/s;    272 sec
[2020-12-07 08:17:26,604 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.valid.0.pt
[2020-12-07 08:17:27,512 INFO] number of examples: 8014
[2020-12-07 08:17:45,586 INFO] Validation perplexity: 1049.57
[2020-12-07 08:17:45,586 INFO] Validation accuracy: 15.6274
[2020-12-07 08:17:45,646 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_1000.pt
[2020-12-07 08:17:47,618 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:17:47,794 INFO] number of examples: 4835
[2020-12-07 08:

[2020-12-07 08:21:44,671 INFO] number of examples: 4835
[2020-12-07 08:21:52,325 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:21:52,606 INFO] number of examples: 4835
[2020-12-07 08:21:55,714 INFO] Step 1900/50000; acc:  88.88; ppl:  1.87; xent: 0.63; lr: 0.00023; 29336/8227 tok/s;    541 sec
[2020-12-07 08:21:55,772 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_1900.pt
[2020-12-07 08:22:02,017 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:22:02,207 INFO] number of examples: 4835
[2020-12-07 08:22:10,079 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:22:10,248 INFO] number of examples: 4835
[2020-12-07 08:22:11,058 INFO] Step 1950/50000; acc:  90.76; ppl:  1.74; xent: 0.55; lr: 0.00024; 25293/7161 tok/s;    556 sec
[2020-12-07 08:22:17,622 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:22:17,896 INFO] number of 

[2020-12-07 08:26:38,247 INFO] Step 2800/50000; acc:  99.14; ppl:  1.17; xent: 0.15; lr: 0.00035; 29820/8429 tok/s;    824 sec
[2020-12-07 08:26:38,307 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_2800.pt
[2020-12-07 08:26:43,803 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:26:43,976 INFO] number of examples: 4835
[2020-12-07 08:26:51,613 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:26:51,790 INFO] number of examples: 4835
[2020-12-07 08:26:56,386 INFO] Step 2850/50000; acc:  99.20; ppl:  1.16; xent: 0.15; lr: 0.00035; 21390/6033 tok/s;    842 sec
[2020-12-07 08:26:59,184 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:26:59,460 INFO] number of examples: 4835
[2020-12-07 08:27:07,103 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 08:27:07,277 INFO] number of examples: 4835
[2020-12-07 08:27:09,882 INFO] Step 2900/

...

[2020-12-07 12:06:49,815 INFO] number of examples: 4835
[2020-12-07 12:06:57,198 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:06:57,378 INFO] number of examples: 4835
[2020-12-07 12:06:57,662 INFO] Step 46050/50000; acc:  99.97; ppl:  1.01; xent: 0.01; lr: 0.00041; 11383/3226 tok/s;  14043 sec
[2020-12-07 12:07:05,069 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:07:05,371 INFO] number of examples: 4835
[2020-12-07 12:07:10,720 INFO] Step 46100/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00041; 29703/8397 tok/s;  14056 sec
[2020-12-07 12:07:10,780 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_46100.pt
[2020-12-07 12:07:14,963 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:07:15,147 INFO] number of examples: 4835
[2020-12-07 12:07:22,775 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:07:22,961 INFO] number 

[2020-12-07 12:11:24,314 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:11:24,490 INFO] number of examples: 4835
[2020-12-07 12:11:26,341 INFO] Step 47000/50000; acc:  99.99; ppl:  1.01; xent: 0.01; lr: 0.00041; 29425/8259 tok/s;  14312 sec
[2020-12-07 12:11:26,343 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.valid.0.pt
[2020-12-07 12:11:27,393 INFO] number of examples: 8014
[2020-12-07 12:11:45,511 INFO] Validation perplexity: 3072.54
[2020-12-07 12:11:45,511 INFO] Validation accuracy: 14.6738
[2020-12-07 12:11:45,573 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_47000.pt
[2020-12-07 12:11:53,295 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:11:53,491 INFO] number of examples: 4835
[2020-12-07 12:12:00,351 INFO] Step 47050/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00041; 11409/3225 tok/s;  14346 sec
[2020-12-07 12:12:00,843 INFO] Loading dataset from OpenNMT-py/Data

[2020-12-07 12:16:01,974 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_47900.pt
[2020-12-07 12:16:06,082 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:16:06,366 INFO] number of examples: 4835
[2020-12-07 12:16:13,770 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:16:13,957 INFO] number of examples: 4835
[2020-12-07 12:16:17,292 INFO] Step 47950/50000; acc:  99.99; ppl:  1.01; xent: 0.01; lr: 0.00040; 25279/7078 tok/s;  14603 sec
[2020-12-07 12:16:21,545 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:16:21,839 INFO] number of examples: 4835
[2020-12-07 12:16:29,183 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:16:29,360 INFO] number of examples: 4835
[2020-12-07 12:16:30,463 INFO] Step 48000/50000; acc:  99.99; ppl:  1.01; xent: 0.01; lr: 0.00040; 29470/8366 tok/s;  14616 sec
[2020-12-07 12:16:30,465 INFO] Loading

[2020-12-07 12:20:49,756 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:20:49,941 INFO] number of examples: 4835
[2020-12-07 12:20:57,264 INFO] Step 48850/50000; acc:  99.99; ppl:  1.01; xent: 0.01; lr: 0.00040; 24788/7043 tok/s;  14883 sec
[2020-12-07 12:20:57,764 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:20:58,086 INFO] number of examples: 4835
[2020-12-07 12:21:05,552 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:21:05,732 INFO] number of examples: 4835
[2020-12-07 12:21:10,753 INFO] Step 48900/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00040; 28765/8103 tok/s;  14896 sec
[2020-12-07 12:21:10,812 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_48900.pt
[2020-12-07 12:21:16,785 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:21:16,978 INFO] number of examples: 4835
[2020-12-07 12:21:24,397 INFO] Loading

[2020-12-07 12:25:39,185 INFO] number of examples: 4835
[2020-12-07 12:25:42,542 INFO] Step 49750/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00040; 23032/6463 tok/s;  15168 sec
[2020-12-07 12:25:46,582 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:25:46,759 INFO] number of examples: 4835
[2020-12-07 12:25:54,477 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:25:54,656 INFO] number of examples: 4835
[2020-12-07 12:25:55,738 INFO] Step 49800/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00040; 29412/8338 tok/s;  15181 sec
[2020-12-07 12:25:55,798 INFO] Saving checkpoint OpenNMT-py/Data/jamo2morph/model/model_step_49800.pt
[2020-12-07 12:26:04,218 INFO] Loading dataset from OpenNMT-py/Data/jamo2morph/demo.train.0.pt
[2020-12-07 12:26:04,495 INFO] number of examples: 4835
[2020-12-07 12:26:10,851 INFO] Step 49850/50000; acc:  99.98; ppl:  1.01; xent: 0.01; lr: 0.00040; 25667/7235 tok/s;  15196 sec
[2020

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [18]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/jamo2morph/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-jamo.txt -output OpenNMT-py/Data/jamo2morph/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 15:43:43,108 INFO] Translating shard 0.
[2020-12-11 15:43:43,676 INFO] 
SENT 1: ['"', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄹ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅗ', 'ㅁ', 'ㅕ', 'ㄴ', ',', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㅅ', 'ㅣ', 'ㅂ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅈ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅁ', 'ㅆ', 'ㅣ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄱ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅡ', 'ㅁ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㄹ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅊ', 'ㅣ', 'ㅇ', 'ㅝ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅜ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄴ', 'ㅆ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄹ', 'ㄷ', 'ㅏ', 'ㅌ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 1: " In other words , Jeju , Eumseong and Hapcheon a

[2020-12-11 15:43:43,977 INFO] 
SENT 31: ['"', 'ㄷ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅋ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄴ', ',', 'ᴥ', 'ㅈ', 'ㅜ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅊ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅕ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㅇ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㄱ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㅇ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅁ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅢ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄴ', 'ㅌ', 'ㅐ', 'ㄱ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㅅ', 'ㅟ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄴ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 31: " It is the same as when Ichiro won the batting title for the first time in his career . "
PRED SCORE: -0.0983

[2020-12-11 15:43:43,978 INFO] 
SENT 32: ['"', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅟ', 'ㅇ', 'ㅓ', 'ㅂ', 'ᴥ', 'ㅎ', 'ㅢ', 'ㅁ', 'ㅏ', 'ㅇ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅔ', 'ㄷ', 'ㅏ', 'ᴥ', 'ㄱ', 

[2020-12-11 15:43:44,269 INFO] 
SENT 61: ['ㅇ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㄱ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄱ', 'ㅊ', 'ㅗ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅎ', 'ㅐ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅐ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄴ', 'ㅗ', 'ㅍ', 'ㄷ', 'ㅏ', '.']
PRED 61: Korean Wave is high in Hanoi , Vietnam .
PRED SCORE: -0.0919

[2020-12-11 15:43:44,269 INFO] 
SENT 62: ['ㄷ', 'ㅐ', 'ㅈ', 'ㅓ', 'ㄴ', 'ㅈ', 'ㅣ', 'ㅇ', 'ㅕ', 'ㄱ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅎ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㄹ', 'ㅣ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅗ', 'ㅇ', 'ㄱ', 'ㅖ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅇ', 'ㅕ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅇ', 'ㅓ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅇ', 'ㅗ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅏ', '.']
PRED 62: The only exception is when the ball is in a hazard .
PRED SCORE: -0.1001

[2020-1

[2020-12-11 15:43:44,536 INFO] 
SENT 91: ['"', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㄱ', 'ㅎ', 'ㅢ', 'ᴥ', 'j', 't', 'b', 'c', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㄹ', 'ㅗ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅗ', 'ㄱ', 'ㅎ', 'ㅐ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅣ', 'ㄹ', 'ㅐ', 'ㄴ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅈ', 'ㅏ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅂ', 'ㅏ', 'ㄱ', ',', 'ᴥ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅖ', 'ㅎ', 'ㅞ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅁ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅁ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅅ', 'ㅗ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', '.', '"']
PRED 91: Several candidates are climbing the new command tower .
PRED SCORE: -0.1003

[2020-12-11 15:43:44,536 INFO] 
SENT 92: ['ㄱ', 'ㅕ', 'ㅇ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄴ', 'ㄷ', 'ㅗ', 'ㄷ', 'ㅡ', 

[2020-12-11 15:43:44,820 INFO] 
SENT 121: ['ㄱ', 'ㅡ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅏ', 'ㅈ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅌ', 'ㅡ', 'ㄱ', 'ㅂ', 'ㅕ', 'ㄹ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅅ', 'ㅜ', 'ㄹ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㅏ', 'ㅃ', 'ㅜ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄹ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄷ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㄲ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅁ', 'ㅇ', 'ㅕ', 'ㅎ', 'ㅏ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅣ', 'ㄷ', 'ㅏ', '.']
PRED 121: " As precedent shows , a country lives only when manufacturing industries live . "
PRED SCORE: -0.0981

[2020-12-11 15:43:44,821 INFO] 
SENT 122: ['"', 'ㅂ', 'ㅜ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅜ', 'ㄷ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅏ', 'ㄱ', 'ㄱ', 

...

SENT 7906: ['ㅇ', 'ㅣ', 'ㄱ', 'ㅏ', 'ㅌ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅎ', 'ㅡ', 'ㄹ', 'ㅡ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅎ', 'ㅗ', 'ㄹ', 'ㄹ', 'ㅗ', 'ㅅ', 'ㅓ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅇ', 'ㅝ', 'ㄴ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅐ', 'ㄹ', 'ㅗ', 'ㅇ', 'ㅜ', 'ㄴ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㄴ', 'ㅌ', 'ㅔ', 'ㅋ', 'ㅡ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅈ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄹ', 'ㅛ', 'ㅇ', 'ᴥ', 'ㅇ', 'ㅡ', 'ㄴ', 'ㅎ', 'ㅐ', 'ㅇ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅐ', 'ㄴ', 'ㅊ', 'ㅏ', 'ㅇ', 'ㅣ', 'ㅈ', 'ㅡ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㄱ', 'ㅐ', 'ㄱ', 'ᴥ', 'ㅂ', 'ㅔ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄱ', 'ㅎ', 'ㅕ', 'ᴥ', 'ㅈ', 'ㅔ', 'ㄷ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅈ', 'ㅐ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅓ', 'ㅄ', 'ㅇ', 'ㅡ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅗ', 'ㅇ', 'ㅕ', 'ㅈ', 'ㅜ', 'ㄴ', 'ㄷ', 'ㅏ', '.']
PRED 7906: The whole team is brightly smiling as Oh Jae - il makes a comeback .
PRED SCORE: -0.0994

[2020-12-11 15:45:00,516 INFO] 
SENT 7907: ['"', 'ㅇ'

[2020-12-11 15:45:00,803 INFO] 
SENT 7921: ['ㄱ', 'ㅝ', 'ㄴ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㅋ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅌ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅡ', 'ㅁ', 'ㅏ', 'ㅌ', 'ㅡ', 'ㅁ', 'ㅣ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅗ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅌ', 'ㅡ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄱ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'k', 't', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㄱ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅑ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'i', 'c', 't', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅑ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅙ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㄱ', 'ㅏ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄺ', 'ㅎ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', '.']
PRED 7921: The structure is equipped with a CD in a booklet that is the level of a photo book .
PRED SCORE: -0.0999

[2020-12-11 15:45:00,804 INFO] 
SE

[2020-12-11 15:45:01,094 INFO] 
SENT 7951: ['ㅋ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', '4', 'ㄱ', 'ㅕ', 'ㅇ', 'ㄱ', 'ㅣ', 'ㅅ', 'ㅓ', 'ᴥ', '1', '0', 'ㄱ', 'ㅗ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅓ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅂ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅑ', 'ㄱ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ᴥ', 'ㄸ', 'ㅐ', 'ㅁ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅎ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅏ', '.']
PRED 7951: The biggest round moon of the year will rise in night of the 20th .
PRED SCORE: -0.0979

[2020-12-11 15:45:01,094 INFO] 
SENT 7952: ['ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅈ', 'ㅔ', 'ㅈ', 'ㅗ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅝ', 'ㄴ

[2020-12-11 15:45:01,406 INFO] 
SENT 7981: ['"', 'ㄱ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅗ', 'ㄱ', 'ㅂ', 'ㅗ', 'ㅈ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ᴥ', '2', '0', '1', '0', 'ㄴ', 'ㅕ', 'ㄴ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅇ', 'ㅈ', 'ㅜ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅎ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', ',', 'ᴥ', 'ㄱ', 'ㅡ', 'ㄷ', 'ㅗ', 'ㅇ', 'ㅇ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅈ', 'ㅗ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅈ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅈ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄶ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅓ', 'ㄹ', 'ㅕ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㄲ', 'ㅇ', '

[2020-12-11 15:45:01,611 INFO] 
SENT 8011: ['ㄷ', 'ㅏ', 'ㅁ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅇ', 'ㅠ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅂ', 'ㅇ', 'ㅢ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅂ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅛ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㅂ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅇ', 'ㅟ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅈ', 'ㅔ', 'ㅈ', 'ㅐ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅇ', 'ㅚ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄴ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㄹ', 'ㅇ', 'ㅛ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', '.']
PRED 8011: " As sanctions against North Korea are effective , the room for manoeuvre is not wide . "
PRED SCORE: -0.0993

[2020-12-11 15:45:01,611 INFO] 
SENT 8012: ['ㅊ', 'ㅜ', 'ㄹ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㄱ', 'ㅘ', 'ᴥ', 

# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [7]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/pred.txt

# Post-processing

In [4]:
# f = open('OpenNMT-py/Data/tgt-test-char.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/tgt-test-char1.txt", "w") as f:
#     f.write(txt)
    
f = open('OpenNMT-py/Data/tgt-test.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'"according to descriptions by the police, mr. kim, who visited the pc-bang as a guest, had an argument with mr. shin while demanding that food left by other guests be cleared from his seat."\n"as jamsil girls\' high school (principal kim in-bong) is aiming to cultivate talents and good personality, the teachers and students are upgrading their career path programs through the ""team-play of trust""."\nformer lawmaker kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed.\n"the working environment of daejeon industrial park in daedeok-gu, daejeon will be improved."\n"around 90t of reinforcement facilities were lost due to high waves at the dongbang breakwater construction site in wimi port, namwon-eup, seogwipo-si, and a 100m median strip fell in the area of nohyeong rotary - samsung service center in jeju."\nit is a program to make students value physical education and art.\n"the us department of justice prosecuted assang

In [19]:
f = open('OpenNMT-py/Data/jamo2morph/pred_50k.txt', 'r', encoding='utf-8')
txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/jamo2morph/pred_50k-edited.txt", "w") as f:
    f.write(txt)

f = open('OpenNMT-py/Data/jamo2char/pred_50k-edited.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'the kim\'s very and sot the first of minderest.\nchoi have to go can a seem.\n"that\'s about kim sellis has ain first age."\nit\'s so have to change that he first year.\nit was for a should such a keep well to the reas.\nthe because is to preasons for the costing.\n"came of the but review, it\'s proparted 10 people."\n"the two more at 17 the can lost work in loved."\nthe useas the is monthing at coulding to stopices.\n"a the care, the two should pizal in the distor."\n"he change, shis can be a lot a lot of world at."\ni also something and that face the possing juse.\n"he fact, is treestion insials are of my being."\n"secuse to help came be drealts not to last."\n"in a fact, a little several are of the bunde."\n"about the 50,000 of should good me first but."\nthe chance seeions are the face in know.\n"now, his being is always to could not far a lot."\nsech kim\'s seed a for the of oviceors is not it.\nchoi has a presed as the first a seviculed again.\n"when first or every what the firs

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [20]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test.txt < OpenNMT-py/Data/jamo2morph/pred_50k-edited.txt

BLEU = 0.07, 13.0/0.7/0.0/0.0 (BP=0.340, ratio=0.481, hyp_len=109285, ref_len=227303)
